In [1]:
import copy

'''
SIMULATE_POPULATION.PY: Simulate a population of cells with the Punisher and a burdensome gene
'''
# By Kirill Sechkar

# PACKAGE IMPORTS ------------------------------------------------------------------------------------------------------
import numpy as np
import jax
import jax.numpy as jnp
import functools
from diffrax import diffeqsolve, Dopri5, ODETerm, SaveAt, PIDController, SteadyStateEvent
import pandas as pd
from bokeh import plotting as bkplot, models as bkmodels, layouts as bklayouts, io as bkio
from bokeh.colors import RGB as bkRGB

# set up bokeh output to notebook
bkio.reset_output()
bkio.output_notebook() 

import time

# import os
# import multiprocessing
# os.environ["XLA_FLAGS"] = "-- python==3.9xla_force_host_platform_device_count={}".format(multiprocessing.cpu_count())

# set up jax
from jax.lib import xla_bridge
jax.config.update('jax_platform_name', 'cpu')
jax.config.update("jax_enable_x64", True)
print(xla_bridge.get_backend().platform)

# CIRCUIT AND EXTERNAL INPUT IMPORTS -----------------------------------------------------------------------------------
from cell_model import *
import synthetic_circuits as circuits

# population simulator
from pop_simulator import *

Loading BokehJS ...

An NVIDIA GPU may be present on this machine, but a CUDA-enabled jaxlib is not installed. Falling back to cpu.


cpu


In [2]:
# INITIALISE CELL MODEL, LOAD THE CIRCUIT

# initialise cell model
cellmodel_auxil = CellModelAuxiliary()  # auxiliary tools for simulating the model and plotting simulation outcomes
par = cellmodel_auxil.default_params()  # get default parameter values
init_conds = cellmodel_auxil.default_init_conds(par)  # get default initial conditions

# load synthetic gene circuit
ode_with_circuit, circuit_F_calc, par, init_conds, circuit_genes, circuit_miscs, circuit_name2pos, circuit_styles, _ = cellmodel_auxil.add_circuit(
    circuits.punisher_xtra_initialise,
    circuits.punisher_xtra_ode,
    circuits.punisher_xtra_F_calc,
    par, init_conds)  # load the circuit

In [3]:
# PARAMETERISE THE CIRCUIT

# BURDENSOME SYNTHETIC GENE
par['c_xtra'] = 1
par['a_xtra'] = 1e5

# PUNISHER
# switch gene conc
par['c_switch'] = 10.0  # gene concentration (nM)
par['a_switch'] = 400.0  # promoter strength (unitless)
par['d_switch']=0.01836
# integrase - expressed from the switch gene's operon, not its own gene => c_int, a_int irrelevant
par['k+_int'] = par['k+_switch']/80.0  # RBS weaker than for the switch gene
par['d_int'] = 0.0#0.01836 # rate of integrase degradation per protease molecule (1/nM/h)
# CAT (antibiotic resistance) gene
init_conds['cat_pb'] = 10.0  # gene concentration (nM) - INITIAL CONDITION< NOT PARAMETER as it can be cut out by the integrase
par['a_cat'] = 500.0  # promoter strength (unitless)
# synthetic protease gene
par['c_prot'] = 10.0  # gene concentration (nM)
par['a_prot'] = 25.0  # promoter strength (unitless)
init_conds['p_prot'] = 1500.0 # if zero at start, the punisher's triggered prematurely

# punisher's transcription regulation function
par['K_switch'] = 300.0  # Half-saturation constant for the self-activating switch gene promoter (nM)
par['eta_switch'] = 2 # Hill coefficient for the self-activating switch gene promoter (unitless)
par['baseline_switch'] = 0.025  # Baseline value of the switch gene's transcription activation function
par['baseline_switch_alt'] = 0
par['p_switch_ac_frac'] = 0.85  # active fraction of protein (i.e. share of molecules bound by the inducer)

# CULTURE MEDIUM
init_conds['s'] = 0.5
par['h_ext'] = 10.5 * (10.0 ** 3)

In [4]:
# INITIALISE DICTIONARIES OF CELLULAR VARIABLE VALUES IN DIFFERENT STATES

# cell growth rates
growth_rates={
    'BSPC': {'H': 0, 'L': 0, '0':0},
    'BOPC': {'H': 0, 'L': 0, '0':0},
    'BSOC': {'H': 0, 'L': 0, '0':0},
    'BOOC': {'H': 0, 'L': 0, '0':0},
    'OSPC': {'H': 0, 'L': 0, '0':0},
    'OOPC': {'H': 0, 'L': 0, '0':0},
    'OSOC': {'H': 0, 'L': 0, '0':0},
    'OOOC': {'H': 0, 'L': 0, '0':0},
    'BSPO': {'H': 0, 'L': 0, '0':0},
    'BOPO': {'H': 0, 'L': 0, '0':0},
    'BSOO': {'H': 0, 'L': 0, '0':0},
    'BOOO': {'H': 0, 'L': 0, '0':0},
    'OSPO': {'H': 0, 'L': 0, '0':0},
    'OOPO': {'H': 0, 'L': 0, '0':0},
    'OSOO': {'H': 0, 'L': 0, '0':0},
    'OOOO': {'H': 0, 'L': 0, '0':0}
}
# record integrase activity rates
integrase_activities=copy.deepcopy(growth_rates)

# burdensome protein levels
p_xtras=copy.deepcopy(growth_rates)

In [5]:
# DETERMINISTIC SIMULATION - WITH CAT PRESENT, FIND ALL TRUE SWITCH EQUILIBRIA FOR ALL GENETIC STATES
# SET SIMULATION PARAMETERS
# diffrax simulator
savetimestep = 1  # save time step
rtol = 1e-6  # relative tolerance for the ODE solver
atol = 1e-6  # absolute tolerance for the ODE solver
# simulation time frames
tf = (0,50) # time frame for simulation before burdensome gene loss

# BSPC: H
#simulate
par_bspc=par.copy()
par_bspc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
init_conds['p_switch']=3000
sol = ode_sim(par_bspc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bspc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bspc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bspc_h = l  # growth rate
p_xtra_bspc_h =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_bspc_h = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# BSPC: L
#simulate
init_conds['p_switch']=0
sol = ode_sim(par_bspc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bspc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bspc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bspc_l = l  # growth rate
p_xtra_bspc_l =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_bspc_l = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# OSPC: H
#simulate
par_ospc=par.copy()
par_ospc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_ospc['func_xtra'] = 0
init_conds['p_switch']=3000
sol = ode_sim(par_ospc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_ospc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bspc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_ospc_h = l  # growth rate
p_xtra_ospc_h =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_ospc_h = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# BOPC: 0
#simulate
par_bopc=par.copy()
par_bopc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_bopc['func_switch'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_bopc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bopc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bopc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bopc_0 = l  # growth rate
p_xtra_bopc_0 =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_bopc_0 = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# OOPC: 0
#simulate
par_oopc=par.copy()
par_oopc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_oopc['func_xtra'] = 0
par_oopc['func_switch'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_oopc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_oopc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_oopc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_oopc_0 = l  # growth rate
p_xtra_oopc_0 =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_oopc_0 = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# BSOC: H
#simulate
par_bsoc=par.copy()
par_bsoc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_bsoc['func_prot'] = 0
init_conds['p_switch']=0.0
sol = ode_sim(par_bsoc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bsoc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bsoc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bsoc_h = l  # growth rate
p_xtra_bsoc_h =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_bsoc_h = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# OSOC:H
#simulate
par_osoc=par.copy()
par_osoc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_osoc['func_xtra'] = 0
par_osoc['func_prot'] = 0
init_conds['p_switch']=0.0
sol = ode_sim(par_osoc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_osoc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_osoc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_osoc_h = l  # growth rate
p_xtra_osoc_h =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_osoc_h = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# BOOC: 0
#simulate
par_booc=par.copy()
par_booc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_booc['func_switch'] = 0
par_booc['func_prot'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_booc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_booc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_booc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_booc_0 = l  # growth rate
p_xtra_booc_0 =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_booc_0 = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

# OOOC: 0
#simulate
par_oooc=par.copy()
par_oooc['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_oooc['func_xtra'] = 0
par_oooc['func_switch'] = 0
par_oooc['func_prot'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_oooc,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_oooc, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_oooc, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_oooc_0 = l  # growth rate
p_xtra_oooc_0 =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
intact_oooc_0 = intact_calc(xs[-1,circuit_name2pos['p_int']],l,par,init_conds['cat_pb'])

/mnt/c/Users/ersat/CODE/punisher/Fig5/pop_simulator.py:667: RuntimeWarning: divide by zero encountered in scalar divide
  exp_time_to_all_cutouts=(1/(intact_rate)) * np.sum(1/np.arange(1,c_cat_pb_int+0.1,1)) # expected time to all cutouts - i.e. expected maximimum of c_cat exp. dist. samples


In [6]:
# FOR CAT GENE PRESENT, RECORD GROWTH RATES, BURDENSOME PROTEIN LEVELS AND INTEGRASE ACTIVITIES FOR ALL STATES

# BSPC: H
growth_rates['BSPC']['H'] = l_bspc_h
p_xtras['BSPC']['H'] = p_xtra_bspc_h
integrase_activities['BSPC']['H'] = intact_bspc_h

# BSPC: L
growth_rates['BSPC']['L'] = l_bspc_l
p_xtras['BSPC']['L'] = p_xtra_bspc_l
integrase_activities['BSPC']['L'] = intact_bspc_l

# BSPC:0
# not considered

# OSPC: H
growth_rates['OSPC']['H'] = l_ospc_h
p_xtras['OSPC']['H'] = 0
integrase_activities['OSPC']['H'] = intact_ospc_h

# OSPC:L
growth_rates['OSPC']['L'] = l_ospc_h # same as OSPC:H
p_xtras['OSPC']['L'] = 0
integrase_activities['OSPC']['L'] = intact_bspc_l

# OSPC:0
# not considered

# BOPC: H
growth_rates['BOPC']['H'] = l_bopc_0
p_xtras['BOPC']['H'] = p_xtra_bopc_0
integrase_activities['BOPC']['H'] = intact_bspc_h

# BOPC: L
growth_rates['BOPC']['L'] = l_bopc_0
p_xtras['BOPC']['L'] = p_xtra_bopc_0
integrase_activities['BOPC']['L'] = intact_bspc_l

# BOPC: 0
growth_rates['BOPC']['0'] = l_bopc_0
p_xtras['BOPC']['0'] = p_xtra_bopc_0
integrase_activities['BOPC']['0'] = 0

# OOPC: H
growth_rates['OOPC']['H'] = l_oopc_0
p_xtras['OOPC']['H'] = 0
integrase_activities['OOPC']['H'] = intact_ospc_h

# OOPC: L
growth_rates['OOPC']['L'] = l_oopc_0
p_xtras['OOPC']['L'] = 0
integrase_activities['OOPC']['L'] = intact_bspc_l

# OOPC: 0
growth_rates['OOPC']['0'] = l_oopc_0
p_xtras['OOPC']['0'] = 0
integrase_activities['OOPC']['0'] = 0

# BSOC: H
growth_rates['BSOC']['H'] = l_bsoc_h
p_xtras['BSOC']['H'] = p_xtra_bsoc_h
integrase_activities['BSOC']['H'] = intact_bsoc_h

# BSOC: L
growth_rates['BSOC']['L'] = l_bspc_l
p_xtras['BSOC']['L'] = p_xtra_bspc_l
integrase_activities['BSOC']['L'] = intact_bspc_l

# BSOC: 0
# not considered

# OSOC: H
growth_rates['OSOC']['H'] = l_osoc_h
p_xtras['OSOC']['H'] = 0
integrase_activities['OSOC']['H'] = intact_osoc_h

# OSOC: L
growth_rates['OSOC']['L'] = l_ospc_h
p_xtras['OSOC']['L'] = 0
integrase_activities['OSOC']['L'] = intact_bspc_l

# OSOC: 0
# not considered

# BOOC: H
growth_rates['BOOC']['H'] = l_booc_0
p_xtras['BOOC']['H'] = p_xtra_booc_0
integrase_activities['BOOC']['H'] = intact_bsoc_h

# BOOC: L
growth_rates['BOOC']['L'] = l_booc_0
p_xtras['BOOC']['L'] = p_xtra_booc_0
integrase_activities['BOOC']['L'] = intact_bspc_l

# BOOC: 0
growth_rates['BOOC']['0'] = l_booc_0
p_xtras['BOOC']['0'] = p_xtra_booc_0
integrase_activities['BOOC']['0'] = 0

# OOOC: H
growth_rates['OOOC']['H'] = l_osoc_h
p_xtras['OOOC']['H'] = 0
integrase_activities['OOOC']['H'] = intact_osoc_h

# OOOC: L
growth_rates['OOOC']['L'] = l_ospc_h
p_xtras['OOOC']['L'] = 0
integrase_activities['OOOC']['L'] = intact_bspc_l

# OOOC: 0
growth_rates['OOOC']['0'] = l_oooc_0
p_xtras['OOOC']['0'] = 0
integrase_activities['OOOC']['0'] = 0

In [7]:
# DETERMINISTIC SIMULATION - WITH NO CAT PRESENT, FIND EQUILIBIRA (THERE'LL ONLY BE A SINGLE POSSIBLE SWITCH STATE) AND RECORD VALUES
# we don't care about integrase activity rates here, as the cat gene is not present - so they will all remain at zero

# BSPO
#simulate
par_bspo=par.copy()
par_bspo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_bspo['func_cat'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_bspo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bspo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bspo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bspo = l  # growth rate
p_xtra_bspo =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
# record
growth_rates['BSPO']['H'] = l_bspo; growth_rates['BSPO']['L'] = l_bspo; growth_rates['BSPO']['0'] = l_bspo
p_xtras['BSPO']['H'] = p_xtra_bspo; p_xtras['BSPO']['L'] = p_xtra_bspo; p_xtras['BSPO']['0'] = p_xtra_bspo

# OSPO
#simulate
par_ospo=par.copy()
par_ospo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_ospo['func_cat'] = 0
par_ospo['func_xtra'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_ospo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_ospo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_ospo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bspo = l  # growth rate
# record
growth_rates['OSPO']['H'] = l_bspo; growth_rates['OSPO']['L'] = l_bspo; growth_rates['OSPO']['0'] = l_bspo
p_xtras['OSPO']['H'] = 0; p_xtras['OSPO']['L'] = 0; p_xtras['OSPO']['0'] = 0

# BOPO
#simulate
par_bopo=par.copy()
par_bopo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_bopo['func_cat'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_bopo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bopo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bopo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bopo = l  # growth rate
p_xtra_bopo =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
# record
growth_rates['BOPO']['H'] = l_bspo; growth_rates['BOPO']['L'] = l_bspo; growth_rates['BOPO']['0'] = l_bspo
p_xtras['BOPO']['H'] = p_xtra_bspo; p_xtras['BOPO']['L'] = p_xtra_bspo; p_xtras['BOPO']['0'] = p_xtra_bspo

# OOPO
#simulate
par_oopo=par.copy()
par_oopo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_oopo['func_cat'] = 0
par_oopo['func_xtra'] = 0
par_oopo['func_switch'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_oopo,
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_oopo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_oopo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_oopo = l  # growth rate
# record
growth_rates['OOPO']['H'] = l_oopo; growth_rates['OOPO']['L'] = l_oopo; growth_rates['OOPO']['0'] = l_oopo
p_xtras['OOPO']['H'] = 0; p_xtras['OOPO']['L'] = 0; p_xtras['OOPO']['0'] = 0

# BSOO
#simulate
par_bsoo=par.copy()
par_bsoo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_bsoo['func_cat'] = 0
par_bsoo['func_prot'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_bsoo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_bsoo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_bsoo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_bsoo = l  # growth rate
p_xtra_bsoo =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
# record
growth_rates['BSOO']['H'] = l_bsoo; growth_rates['BSOO']['L'] = l_bsoo; growth_rates['BSOO']['0'] = l_bsoo
p_xtras['BSOO']['H'] = p_xtra_bsoo; p_xtras['BSOO']['L'] = p_xtra_bsoo; p_xtras['BSOO']['0'] = p_xtra_bsoo

# OSOO
#simulate
par_osoo=par.copy()
par_osoo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_osoo['func_cat'] = 0
par_osoo['func_xtra'] = 0
par_osoo['func_prot'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_osoo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_osoo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_osoo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_osoo = l  # growth rate
# record
growth_rates['OSOO']['H'] = l_osoo; growth_rates['OSOO']['L'] = l_osoo; growth_rates['OSOO']['0'] = l_osoo
p_xtras['OSOO']['H'] = 0; p_xtras['OSOO']['L'] = 0; p_xtras['OSOO']['0'] = 0

# BOOO
#simulate
par_booo=par.copy()
par_booo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_booo['func_cat'] = 0
par_booo['func_switch'] = 0
par_booo['func_prot'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_booo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_booo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_booo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_booo = l  # growth rate
p_xtra_booo =  xs[-1, circuit_name2pos['p_xtra']] # burdensome proein concentration
# record
growth_rates['BOOO']['H'] = l_booo; growth_rates['BOOO']['L'] = l_booo; growth_rates['BOOO']['0'] = l_booo
p_xtras['BOOO']['H'] = p_xtra_booo; p_xtras['BOOO']['L'] = p_xtra_booo; p_xtras['BOOO']['0'] = p_xtra_booo

# OOOO
par_oooo=par.copy()
par_oooo['k_sxf'] = 0 # integrase must be disabled to make sure we stay in the genetic state of interest
par_oooo['func_cat'] = 0
par_oooo['func_xtra'] = 0
par_oooo['func_switch'] = 0
par_oooo['func_prot'] = 0
init_conds['p_switch']=0
sol = ode_sim(par_oooo,  # dictionary with model parameters
              ode_with_circuit,  # ODE function for the cell with synthetic circuit
              cellmodel_auxil.x0_from_init_conds(init_conds, circuit_genes, circuit_miscs),
              # initial condition VECTOR
              len(circuit_genes), len(circuit_miscs), circuit_name2pos,
              # dictionaries with circuit gene and miscellaneous specie names, species name to vector position decoder
              cellmodel_auxil.synth_gene_params_for_jax(par_oooo, circuit_genes),
              # synthetic gene parameters for calculating k values
              tf, jnp.arange(tf[0], tf[1], savetimestep),  # time axis for saving the system's state
              rtol,
              atol)  # simulation parameters: when to save the system's state, relative and absolute tolerances)   # simulation parameters: time frame, save time step, relative and absolute tolerances
ts = np.array(sol.ts)
xs = np.array(sol.ys)
# record values
_, ls, _, _, _, _, _, _ = cellmodel_auxil.get_e_l_Fr_nu_psi_T_D_Dnodeg(ts, xs, par_oooo, circuit_genes, circuit_miscs, circuit_name2pos)
l=np.float64(ls[-1])
l_oooo = l  # growth rate
# record
growth_rates['OOOO']['H'] = l_oooo; growth_rates['OOOO']['L'] = l_oooo; growth_rates['OOOO']['0'] = l_oooo
p_xtras['OOOO']['H'] = 0; p_xtras['OOOO']['L'] = 0; p_xtras['OOOO']['0'] = 0

In [8]:
# CLEAR MEMORY
del par_bspc, par_ospc, par_bopc, par_oopc, par_bsoc, par_osoc, par_booc, par_oooc
del par_bspo, par_ospo, par_bopo, par_oopo, par_bsoo, par_osoo, par_booo, par_oooo

In [9]:
# DEFINE REMAININING STOCHASTIC TRANSITION RATES
# define gene mutation rates
mutation_rates = [1e-12,1e-12,1e-12,1e-12]

# define switch state transition rates (only those that are non-zero)
transition_rates = {
    'BSPC': {
        'L>H': 1/11.357780722265524,
        'H>L': 1/1153.29393262983
    },
    'OSPC': {
        'L>H': 1/5.622805028256774,
        'H>L': 1/29994.9997221792
    },
    'BOPC': {
        'H>L': 1/2.601327,
        'L>0': 1/1.49236560946109
    },
    'OOPC': {
        'H>L': 1/2.40654866666666,
        'L>0': 1/1.27014547395815
    },
    'BSOC': {
        'L>H': 1/3.13026566666666
    },
    'OSOC': {
        'L>H': 1/2.70777133333333
    },
    'BOOC': {
        'H>L': 1/2.70764966666666,
        'L>0': 1/1.48274455791453
    },
    'OOOC': {
        'H>L': 1/2.47044833333333,
        'L>0': 1/1.26857090423757
    },
}

In [10]:
# SIMULATE THE POPULATION WITH THE PUNISHER
pop_sim = PopulationSimulator(
    # optional arguments
    growth_rates=growth_rates,
    mutation_rates=mutation_rates,
    transition_rates=transition_rates,
    integrase_activities=integrase_activities,
    p_xtras=p_xtras
)

# set the simulation parameters
pop_tf = (0, 500)
pop_ts = jnp.arange(pop_tf[0], pop_tf[1], 0.1)
pop_rtol = 1e-6
pop_atol = 1e-6

# set the initial condition - starting with all genes present
x0 = jnp.zeros(pop_sim.num_css).at[pop_sim.cs2p[(1, 1, 1, 1)]['L']].set(1e9)

# x0_bsic = jnp.zeros(pop_sim.num_css).at[pop_sim.cs2p[(1, 1, 1, 1)]['L']].set(1e9/2)
# x0=x0_bsic.at[pop_sim.cs2p[(0, 1, 1, 1)]['L']].set(1e9/2)

pop_sol=pop_ode_sim(x0,pop_tf,pop_ts,pop_rtol,pop_atol,pop_sim)
pop_ts=np.array(pop_sol.ts)
pop_xs=np.array(pop_sol.ys)

In [11]:
# SIMULATE THE POPULATION WITHOUT THE PUNISHER

# set the initial condition - starting with all genes present
x0_no_punisher = jnp.zeros(pop_sim.num_css).at[pop_sim.cs2p[(1, 0, 0, 1)]['0']].set(1e9)

pop_sol_no_punisher=pop_ode_sim(x0_no_punisher,pop_tf,pop_ts,pop_rtol,pop_atol,pop_sim)
pop_ts_no_punisher=np.array(pop_sol_no_punisher.ts)
pop_xs_no_punisher=np.array(pop_sol_no_punisher.ys)

In [17]:
# PLOT THE RESULTS

# genetic states
# bkplot.output_file('population_simulation.html')
func_figure=pop_sim.plot_funcstates(pop_ts,pop_xs,
                                    dimensions=(480,360),
                                    tspan=(0,pop_tf[1]))
# switch states
allfunc_switch_figure=pop_sim.plot_funcstate_switches(pop_ts,pop_xs,
                                                      (0,1,0,1),
                                                      dimensions=(480,360),
                                                      tspan=(0,pop_tf[1]))
# burden gene presence
burden_figure = pop_sim.plot_with_burden(pop_ts, pop_xs,
                                         label1='W/punisher',
                                         #
                                         ts2=pop_ts_no_punisher, xs2=pop_xs_no_punisher,
                                         label2='W/o punisher',
                                         #
                                         dimensions=(480, 270),
                                         tspan=(0, pop_tf[1]))

# average protein synthesis rate per cell
rate_figure = pop_sim.plot_percell_avg_synth_rate(pop_ts, pop_xs,
                                                 label1='W/punisher',
                                                 #
                                                 ts2=pop_ts_no_punisher, xs2=pop_xs_no_punisher,
                                                 label2='W/o punisher',
                                                 #
                                                 dimensions=(480, 270),
                                                 tspan=(0, pop_tf[1]))
# lifetime metrics
yield_figure, decay_figure = pop_sim.plot_metrics(pop_ts, pop_xs,
                                                 share_initial=0.05,
                                                 #
                                                 ts2=pop_ts_no_punisher, xs2=pop_xs_no_punisher,
                                                 label1='W/punisher',
                                                 label2='W/o punisher',
                                                 #
                                                 dimensions=(480, 270),
                                                 tspan=(0, pop_tf[1]))

# show plots
func_figure.output_backend = 'svg'
func_figure.title.text = 'Without punisher'
bkplot.show(bklayouts.grid([[func_figure,   None],
                            [burden_figure, rate_figure],
                            [yield_figure,  decay_figure]]))

In [13]:
# SIMULATE THE POPULATION WITH THE PUNISHER AND WITH OVERLAPS
# cells without the punisher will be unablke to grow
growth_rates_overlaps = copy.deepcopy(growth_rates)
for func in growth_rates_overlaps.keys():
    if(func[1]=='O'):
        growth_rates_overlaps[func]['H'] = 0
        growth_rates_overlaps[func]['L'] = 0
        growth_rates_overlaps[func]['0'] = 0
        
pop_sim_overlaps = PopulationSimulator(
    # optional arguments
    growth_rates=growth_rates_overlaps,
    mutation_rates=mutation_rates,
    transition_rates=transition_rates,
    integrase_activities=integrase_activities,
    p_xtras=p_xtras
)

# set the initial condition - starting with all genes present
x0 = jnp.zeros(pop_sim_overlaps.num_css).at[pop_sim_overlaps.cs2p[(1, 1, 1, 1)]['L']].set(1e9)

pop_sol_overlaps=pop_ode_sim(x0,pop_tf,pop_ts,pop_rtol,pop_atol,pop_sim_overlaps)

pop_ts_overlaps=np.array(pop_sol_overlaps.ts)
pop_xs_overlaps=np.array(pop_sol_overlaps.ys)

In [14]:
# PLOT THE RESULTS WITH OVERLAPS

# genetic states
# bkplot.output_file('population_simulation.html')
func_figure=pop_sim.plot_funcstates(pop_ts_overlaps,pop_xs_overlaps,
                                    dimensions=(480,360),
                                    tspan=(0,pop_tf[1]))
# switch states
allfunc_switch_figure=pop_sim.plot_funcstate_switches(pop_ts_overlaps,pop_xs_overlaps,
                                                      (0,1,0,1),
                                                      dimensions=(480,360),
                                                      tspan=(0,pop_tf[1]))
# burden gene presence
burden_figure = pop_sim.plot_with_burden(pop_ts_overlaps, pop_xs_overlaps,
                                         label1='W/punisher',
                                         #
                                         #ts2=pop_ts_no_punisher, xs2=pop_xs_no_punisher,
                                         #label2='W/o punisher',
                                         #
                                         dimensions=(480, 270),
                                         tspan=(0, pop_tf[1]))

# average protein synthesis rate per cell
rate_figure = pop_sim.plot_percell_avg_synth_rate(pop_ts_overlaps, pop_xs_overlaps,
                                                 label1='W/punisher',
                                                 #
                                                 #ts2=pop_ts_no_punisher, xs2=pop_xs_no_punisher,
                                                 #label2='W/o punisher',
                                                 #
                                                 dimensions=(480, 270),
                                                 tspan=(0, pop_tf[1]))
# lifetime metrics
yield_figure, funcdur_figure = pop_sim.plot_metrics(pop_ts_overlaps, pop_xs_overlaps,
                                                 share_initial=0.95,
                                                 #
                                                 #ts2=pop_ts_no_punisher, xs2=pop_xs_no_punisher,
                                                 label1='W/punisher',
                                                 #label2='W/o punisher',
                                                 #
                                                 dimensions=(480, 270),
                                                 tspan=(0, pop_tf[1]))

# show plots
bkplot.show(bklayouts.grid([[func_figure,   None],
                            [burden_figure, rate_figure],
                            [yield_figure,  funcdur_figure]]))

In [15]:
# CONSIDER AND PLOT DIFFERENT MUTATION RATES

# define the range of mutation rates
mutrate_range=np.logspace(-18,-3,6)

# initialise the storage of yields and function durations
yields_pun=np.zeros_like(mutrate_range)
yields_nopun=np.zeros_like(mutrate_range)
funcdurs_pun=np.zeros_like(mutrate_range)
funcdurs_nopun=np.zeros_like(mutrate_range)

# set simulation parameters
# set the simulation parameters
pop_tf_diffmutrates = (0, 750)
pop_savets_diffmutrates = jnp.arange(pop_tf_diffmutrates[0], pop_tf_diffmutrates[1], 0.1)
pop_rtol_diffmutrates = 1e-6
pop_atol_diffmutrates = 1e-6

# loop through the mutation rates
for mutrate_cntr in range(0,len(mutrate_range)):
    # set the mutation rates
    mutation_rates_diffmutrates = [mutrate_range[mutrate_cntr],mutrate_range[mutrate_cntr],mutrate_range[mutrate_cntr],mutrate_range[mutrate_cntr]]
    # simulate the population with the punisher
    pop_sim_diffmutrates = PopulationSimulator(
        # optional arguments
        growth_rates=growth_rates,
        mutation_rates=mutation_rates_diffmutrates,
        transition_rates=transition_rates,
        integrase_activities=integrase_activities,
        p_xtras=p_xtras
    )
    x0 = jnp.zeros(pop_sim_diffmutrates.num_css).at[pop_sim_diffmutrates.cs2p[(1, 1, 1, 1)]['L']].set(1e9)
    pop_sol_diffmutrates=pop_ode_sim(x0,
                                     pop_tf_diffmutrates,pop_savets_diffmutrates,
                                     pop_rtol_diffmutrates,pop_atol_diffmutrates,
                                     pop_sim_diffmutrates)
    pop_ts_diffmutrates=np.array(pop_sol_diffmutrates.ts)
    pop_xs_diffmutrates=np.array(pop_sol_diffmutrates.ys)
    # get metrics with the punisher
    avg_synthrates_percell=pop_sim_diffmutrates.percell_avg_synth_rate(pop_ts_diffmutrates,pop_xs_diffmutrates)
    yields_pun[mutrate_cntr]=pop_sim_diffmutrates.percell_yield(pop_ts_diffmutrates,avg_synthrates_percell)
    funcdurs_pun[mutrate_cntr]=pop_sim_diffmutrates.func_duration(pop_ts_diffmutrates,avg_synthrates_percell,share_initial=0.95)

    # simulate the population without the punisher
    x0_no_punisher = jnp.zeros(pop_sim_diffmutrates.num_css).at[pop_sim_diffmutrates.cs2p[(1, 0, 0, 1)]['0']].set(1e9)
    pop_sol_diffmutrates_no_punisher=pop_ode_sim(x0_no_punisher,
                                                 pop_tf_diffmutrates,pop_savets_diffmutrates,
                                                 pop_rtol_diffmutrates,pop_atol_diffmutrates,
                                                 pop_sim_diffmutrates)
    pop_ts_diffmutrates_no_punisher=np.array(pop_sol_diffmutrates_no_punisher.ts)
    pop_xs_diffmutrates_no_punisher=np.array(pop_sol_diffmutrates_no_punisher.ys)
    # get metrics without the punisher
    avg_synthrates_percell_no_punisher=pop_sim_diffmutrates.percell_avg_synth_rate(pop_ts_diffmutrates_no_punisher,pop_xs_diffmutrates_no_punisher)
    yields_nopun[mutrate_cntr]=pop_sim_diffmutrates.percell_yield(pop_ts_diffmutrates_no_punisher,avg_synthrates_percell_no_punisher)
    funcdurs_nopun[mutrate_cntr]=pop_sim_diffmutrates.func_duration(pop_ts_diffmutrates_no_punisher,avg_synthrates_percell_no_punisher,share_initial=0.95)

In [16]:
# PLOT METRICS AS FUNCTIONS OF MUTATION RATES

# YIELDS
yield_diffmutrates_figure = bkplot.figure(#title='Yields as functions of mutation rates',
                                            x_axis_type='log',
                                            # y_axis_type='log',
                                            x_axis_label='Gene mutation rate', 
                                            y_axis_label='Total protein yield/cell, nM',
                                            frame_width=200,
                                            frame_height=150)
# plot yields with the punisher
yield_diffmutrates_figure.line(mutrate_range, yields_pun,
                                 line_width=2, color='blue',
                                 legend_label='With punisher')
yield_diffmutrates_figure.scatter(mutrate_range, yields_pun, 
                               marker='circle', color='blue',
                               legend_label='With punisher', 
                               line_width=2)
# plot yields without the punisher
yield_diffmutrates_figure.line(mutrate_range, yields_nopun,
                                 line_width=2, color='red',
                                 legend_label='Without punisher')
yield_diffmutrates_figure.scatter(mutrate_range, yields_nopun,
                                    marker='circle', color='red',
                                    legend_label='Without punisher', 
                                    line_width=2)

# mark the scenario for which the previous plots were made
yield_diffmutrates_figure.vspan(mutation_rates[0],color='black', line_dash='dotted', line_width=1.5)

# x axis ticks
yield_diffmutrates_figure.xaxis.ticker = list(mutrate_range)

# legend settings
yield_diffmutrates_figure.legend.location = 'top_right'
yield_diffmutrates_figure.legend.label_text_font_size = '8pt'
yield_diffmutrates_figure.legend.glyph_width = 10
yield_diffmutrates_figure.legend.padding = 3
yield_diffmutrates_figure.legend.spacing = 3
yield_diffmutrates_figure.legend.margin = 3

# FUNCTION DURATIONS
funcdur_diffmutrates_figure = bkplot.figure(#title='Function durations as functions of mutation rates',
                                            x_axis_type='log',
                                            x_axis_label='Gene mutation rate', 
                                            y_axis_label='Function duration, h',
                                            frame_width=200, 
                                            frame_height=150)
# plot function durations with the punisher
funcdur_diffmutrates_figure.line(mutrate_range, funcdurs_pun,
                                 line_width=2, color='blue',
                                 legend_label='With punisher')
funcdur_diffmutrates_figure.scatter(mutrate_range, funcdurs_pun,
                                 marker='circle', color='blue',
                                 legend_label='With punisher', 
                                 line_width=2)
# plot function durations without the punisher
funcdur_diffmutrates_figure.line(mutrate_range, funcdurs_nopun,
                                 line_width=2, color='red',
                                 legend_label='Without punisher')
funcdur_diffmutrates_figure.scatter(mutrate_range, funcdurs_nopun,
                                    marker='circle', color='red',
                                    legend_label='Without punisher', 
                                    line_width=2)

# mark the scenario for which the previous plots were made
funcdur_diffmutrates_figure.vspan(mutation_rates[0],color='black', line_dash='dotted', line_width=1.5)

# x axis ticks
funcdur_diffmutrates_figure.xaxis.ticker = list(mutrate_range)

# legend settings
funcdur_diffmutrates_figure.legend.location = 'top_right'
funcdur_diffmutrates_figure.legend.label_text_font_size = '8pt'
funcdur_diffmutrates_figure.legend.glyph_width = 10
funcdur_diffmutrates_figure.legend.padding = 3
funcdur_diffmutrates_figure.legend.spacing = 3
funcdur_diffmutrates_figure.legend.margin = 3

# show plots
yield_diffmutrates_figure.output_backend = 'svg'
funcdur_diffmutrates_figure.output_backend = 'svg'
bkplot.show(bklayouts.grid([[yield_diffmutrates_figure, funcdur_diffmutrates_figure]]))